In [0]:
from pyspark.ml.linalg import Vectors, VectorUDT
from pyspark.ml.feature import BucketedRandomProjectionLSH

from pyspark.sql import DataFrame
from pyspark.sql.functions import col, udf, max, collect_list, lit, expr, coalesce, pow, sum
from pyspark.sql.types import *

import pandas as pd
import numpy as np

import math
import shutil

In [0]:
@udf(VectorUDT())
def to_vector(size, index_list, value_list):
    ind, val = zip(*sorted(zip(index_list, value_list)))
    return Vectors.sparse(size, ind, val)
    
_ = spark.udf.register('to_vector', to_vector)

# generate ratings vectors 
ratings_vectors = spark.sql('''
  SELECT 
      user_id,
      to_vector(size, index_list, value_list) as ratings,
      size,
      index_list,
      value_list
    FROM ( 
      SELECT
        user_id,
        (SELECT max(product_id) + 1 FROM instacart.products) as size,
        COLLECT_LIST(product_id) as index_list,
        COLLECT_LIST(normalized_purchases) as value_list
      FROM ( -- all users, ratings
        SELECT
          user_id,
          product_id,
          normalized_purchases
        FROM instacart.user_ratings
        WHERE split = 'calibration'
        )
      GROUP BY user_id
      )
    ''')

In [0]:
bucket_length = 0.0025
lsh_tables = 5

lsh = BucketedRandomProjectionLSH(
  inputCol = 'ratings', 
  outputCol = 'hash', 
  numHashTables = lsh_tables, 
  bucketLength = bucket_length
  )

# fit the algorithm to the dataset
fitted_lsh = lsh.fit(ratings_vectors)

# assign LSH buckets to users
hashed_vectors = (
  fitted_lsh
    .transform(ratings_vectors)
    ).cache()

hashed_vectors.createOrReplaceTempView('hashed_vectors')

In [0]:
user_148 = (
  hashed_vectors
    .filter('user_id=148')
    .select('user_id','ratings')
  )

user_148.collect()[0]['ratings']

Out[5]: SparseVector(49689, {132: 0.0814, 274: 0.0814, 781: 0.0814, 1203: 0.0814, 1915: 0.0814, 3376: 0.0814, 4025: 0.0814, 4477: 0.0814, 5201: 0.0814, 6891: 0.0814, 7412: 0.1628, 7539: 0.0814, 7870: 0.1628, 8362: 0.0814, 10129: 0.0814, 10451: 0.0814, 10983: 0.1628, 11109: 0.0814, 11212: 0.0814, 12023: 0.0814, 13577: 0.0814, 14804: 0.0814, 15008: 0.0814, 15438: 0.0814, 17284: 0.0814, 17450: 0.1628, 17828: 0.1628, 18629: 0.1628, 19385: 0.0814, 20310: 0.0814, 20564: 0.0814, 20632: 0.1628, 21295: 0.0814, 21806: 0.2441, 22035: 0.0814, 22217: 0.0814, 22721: 0.0814, 23383: 0.1628, 23459: 0.1628, 24118: 0.0814, 24230: 0.0814, 24413: 0.2441, 25821: 0.0814, 26313: 0.0814, 26638: 0.0814, 27156: 0.0814, 27219: 0.0814, 27845: 0.0814, 28568: 0.0814, 29406: 0.0814, 29721: 0.0814, 29871: 0.0814, 29926: 0.0814, 30391: 0.0814, 30461: 0.0814, 31504: 0.3255, 31990: 0.0814, 32420: 0.0814, 32426: 0.0814, 33407: 0.0814, 34524: 0.0814, 36953: 0.0814, 37119: 0.0814, 37514: 0.0814, 38288: 0.0814, 38481: 0.0814

In [0]:
number_of_customers = 10

# retrieve n nearest customers 
similar_k_users = (
  fitted_lsh.approxNearestNeighbors(
    hashed_vectors, 
    user_148.collect()[0]['ratings'], # must be a vector value (not a dataframe)
    number_of_customers, 
    distCol='distance'
    )
    .select('user_id', 'distance')
  )
  
display(similar_k_users)

user_id distance 148 0.0 75604 1.2190600561395566 183757 1.2228734335140283 4900 1.2415711561941944 44259 1.24379822773884 78995 1.2447867934396357 112316 1.2533600998598375 59880 1.2639667426747596 195292 1.2702051276573025 58390 1.2704275817648039

In [0]:
max_distance_from_target = 1.3

# retreive all users within a distance range
similar_d_users = (
    fitted_lsh.approxSimilarityJoin(
      user_148,
      hashed_vectors,  
      threshold = max_distance_from_target, 
      distCol='distance'
      )
    .selectExpr('datasetA.user_id as user_a', 'datasetB.user_id as user_b', 'distance')
    .orderBy('distance', ascending=True)
    )
  
display(similar_d_users)

user_a user_b distance 148 148 0.0 148 75604 1.2190600561395566 148 183757 1.2228734335140283 148 4900 1.2415711561941944 148 44259 1.24379822773884 148 78995 1.2447867934396357 148 112316 1.2533600998598375 148 59880 1.2639667426747596 148 195292 1.2702051276573025 148 58390 1.2704275817648039 148 171067 1.27080591399375 148 30765 1.2711772180197245 148 159596 1.2718104432978357 148 194179 1.283425203096351 148 198751 1.288260253090212 148 15201 1.289340740897489 148 74174 1.2897967232733192 148 139301 1.29116046724045 148 95883 1.2940187852158629 148 83226 1.2940187852158629 148 187905 1.295544678175903 148 52544 1.2969816114160833 148 179343 1.297303471261663 148 65841 1.2995861357476541

In [0]:
# calculate similarity score
similar_users = (
  similar_k_users
    .withColumn('similarity', lit(1) / (lit(1) + col('distance')))
  )

display(similar_users)

user_id distance similarity 148 0.0 1.0 75604 1.2190600561395566 0.45064125111587783 183757 1.2228734335140283 0.44986816834602705 4900 1.2415711561941944 0.44611566188147667 44259 1.24379822773884 0.4456728718462968 78995 1.2447867934396357 0.4454766051379529 112316 1.2533600998598375 0.4437817107271055 59880 1.2639667426747596 0.4417026015225611 195292 1.2702051276573025 0.4404888297613582 58390 1.2704275817648039 0.4404456711289156

In [0]:
# calculate lowest possible unscaled similarity score
min_score = 1 / (1 + math.sqrt(2))

# calculate similarity score
similar_users = (
  similar_users
    .withColumn(
       'similarity_rescaled', 
       (col('similarity') - lit(min_score)) / lit(1.0 - min_score)
       )
     )

# make available for SQL query
similar_users.createOrReplaceTempView('similar_users')

display(similar_users)

user_id distance similarity similarity_rescaled 148 0.0 1.0 1.0 75604 1.2190600561395566 0.45064125111587783 0.06218595447575728 183757 1.2228734335140283 0.44986816834602705 0.060866219636926545 4900 1.2415711561941944 0.44611566188147667 0.05446029040484622 44259 1.24379822773884 0.4456728718462968 0.05370440053314881 78995 1.2447867934396357 0.4454766051379529 0.0533693523044138 112316 1.2533600998598375 0.4437817107271055 0.050475986562261 59880 1.2639667426747596 0.4417026015225611 0.04692672514035588 195292 1.2702051276573025 0.4404888297613582 0.04485468713599375 58390 1.2704275817648039 0.4404456711289156 0.04478101074188418

In [0]:
similar_ratings = spark.sql('''
      SELECT
        m.user_id,
        m.product_id,
        COALESCE(n.normalized_purchases, 0.0) as normalized_purchases,
        m.similarity_rescaled
      FROM ( -- get complete list of products across similar users
        SELECT
          x.user_id,
          y.product_id,
          x.similarity_rescaled
        FROM (
          SELECT user_id, similarity_rescaled
          FROM similar_users
          ) x
        CROSS JOIN instacart.products y
        ) m
      LEFT OUTER JOIN ( -- retrieve ratings actually provided by similar users
        SELECT x.user_id, x.product_id, x.normalized_purchases 
        FROM instacart.user_ratings x 
        LEFT SEMI JOIN similar_users y 
          ON x.user_id=y.user_id 
        WHERE x.split = 'calibration'
          ) n
        ON m.user_id=n.user_id AND m.product_id=n.product_id
      ''')

display(similar_ratings)

user_id product_id normalized_purchases similarity_rescaled 112316 15 0.0 0.050475986562261 78995 44 0.0 0.0533693523044138 148 59 0.0 1.0 59880 63 0.0 0.04692672514035588 4900 94 0.0 0.05446029040484622 59880 127 0.0 0.04692672514035588 4900 131 0.0 0.05446029040484622 4900 142 0.0 0.05446029040484622 148 146 0.0 1.0 75604 157 0.0 0.06218595447575728 58390 163 0.0 0.04478101074188418 58390 167 0.0 0.04478101074188418 183757 169 0.0 0.060866219636926545 148 173 0.0 1.0 148 194 0.0 1.0 59880 204 0.0 0.04692672514035588 112316 214 0.0 0.050475986562261 44259 226 0.0 0.05370440053314881 78995 226 0.0 0.0533693523044138 148 229 0.0 1.0 59880 293 0.0 0.04692672514035588 75604 304 0.0 0.06218595447575728 112316 310 0.0 0.050475986562261 195292 314 0.0 0.04485468713599375 195292 342 0.0 0.04485468713599375 195292 350 0.0 0.04485468713599375 78995 358 0.0 0.0533693523044138 195292 359 0.0 0.04485468713599375 4900 369 0.0 0.05446029040484622 195292 437 0.0 0.04485468713599375 183757 444 0.0 0.060866219636926545 195292 485 0.0 0.04485468713599375 112316 497 0.0 0.050475986562261 58390 510 0.0 0.04478101074188418 195292 541 0.0 0.04485468713599375 112316 550 0.0 0.050475986562261 75604 563 0.0 0.06218595447575728 58390 566 0.0 0.04478101074188418 195292 568 0.0 0.04485468713599375 195292 636 0.0 0.04485468713599375 58390 654 0.0 0.04478101074188418 4900 674 0.0 0.05446029040484622 59880 675 0.0 0.04692672514035588 78995 728 0.0 0.0533693523044138 44259 748 0.0 0.05370440053314881 78995 755 0.0 0.0533693523044138 58390 761 0.0 0.04478101074188418 58390 782 0.0 0.04478101074188418 112316 799 0.0 0.050475986562261 75604 825 0.0 0.06218595447575728 58390 835 0.0 0.04478101074188418 195292 836 0.0 0.04485468713599375 148 857 0.0 1.0 4900 866 0.0 0.05446029040484622 59880 869 0.0 0.04692672514035588 44259 884 0.0 0.05370440053314881 183757 896 0.0 0.060866219636926545 44259 903 0.0 0.05370440053314881 78995 915 0.0 0.0533693523044138 183757 938 0.0 0.060866219636926545 4900 939 0.0 0.05446029040484622 148 977 0.0 1.0 75604 985 0.0 0.06218595447575728 4900 1003 0.0 0.05446029040484622 112316 1007 0.0 0.050475986562261 183757 1059 0.0 0.060866219636926545 58390 1061 0.0 0.04478101074188418 4900 1096 0.0 0.05446029040484622 59880 1099 0.0 0.04692672514035588 195292 1115 0.0 0.04485468713599375 4900 1117 0.0 0.05446029040484622 75604 1131 0.0 0.06218595447575728 195292 1134 0.0 0.04485468713599375 44259 1166 0.0 0.05370440053314881 78995 1190 0.0 0.0533693523044138 183757 1196 0.0 0.060866219636926545 183757 1239 0.0 0.060866219636926545 112316 1251 0.0 0.050475986562261 59880 1262 0.0 0.04692672514035588 59880 1280 0.0 0.04692672514035588 112316 1360 0.0 0.050475986562261 148 1365 0.0 1.0 58390 1384 0.0 0.04478101074188418 4900 1388 0.0 0.05446029040484622 44259 1405 0.0 0.05370440053314881 78995 1440 0.0 0.0533693523044138 59880 1460 0.0 0.04692672514035588 195292 1478 0.0 0.04485468713599375 183757 1490 0.0 0.060866219636926545 112316 1497 0.0 0.050475986562261 195292 1541 0.0 0.04485468713599375 148 1563 0.0 1.0 4900 1566 0.0 0.05446029040484622 112316 1576 0.0 0.050475986562261 78995 1585 0.0 0.0533693523044138 183757 1592 0.0 0.060866219636926545 148 1605 0.0 1.0 4900 1612 0.0 0.05446029040484622 112316 1617 0.0 0.050475986562261 78995 1618 0.0 0.0533693523044138 183757 1660 0.0 0.060866219636926545 148 1667 0.0 1.0 195292 1674 0.0 0.04485468713599375 148 1688 0.0 1.0 183757 1692 0.0 0.060866219636926545 75604 1694 0.0 0.06218595447575728 44259 1711 0.0 0.05370440053314881 59880 1722 0.0 0.04692672514035588 4900 1748 0.0 0.05446029040484622 183757 1764 0.0 0.060866219636926545 59880 1785 0.0 0.04692672514035588 58390 1799 0.0 0.04478101074188418 148 1894 0.0 1.0 195292 1919 0.0 0.04485468713599375 148 1946 0.0 1.0 148 1997 0.0 1.0 78995 2002 0.0 0.0533693523044138 195292 2030 0.0 0.04485468713599375 4900 2034 0.0 0.05446029040484622 183757 2062 0.0 0.060866219636926545 59880 2078 0.0 0.04692672514035588 4900 2104 0.0 0.05446029040484622 7899

In [0]:
product_ratings = ( 
   similar_ratings
    .groupBy('product_id')
      .agg( 
        sum(col('normalized_purchases') * col('similarity_rescaled')).alias('weighted_rating'),
        sum('similarity_rescaled').alias('total_weight')
        )
    .withColumn('recommendation_score', col('weighted_rating')/col('total_weight'))
    #.select('product_id', 'recommendation_score')
    .orderBy('recommendation_score', ascending=False)
  )

display(product_ratings)

product_id weighted_rating total_weight recommendation_score 24413 0.385672560750228 1.4716246269355877 0.2620726465779026 31504 0.3472890202416005 1.4716246269355875 0.23599022052571375 44557 0.3360943125094087 1.4716246269355875 0.22838318030139856 18629 0.29096643749784246 1.4716246269355875 0.1977178365815551 21806 0.2733979472203292 1.4716246269355877 0.1857796765671384 10983 0.16275769175423188 1.4716246269355873 0.11059728736202765 23383 0.16275769175423188 1.4716246269355873 0.11059728736202765 17828 0.16275769175423188 1.4716246269355875 0.11059728736202763 7412 0.16275769175423188 1.4716246269355875 0.11059728736202763 7870 0.16275769175423188 1.4716246269355875 0.11059728736202763 23459 0.16275769175423188 1.4716246269355875 0.11059728736202763 20632 0.16275769175423188 1.4716246269355875 0.11059728736202763 17450 0.16275769175423188 1.4716246269355875 0.11059728736202763 11212 0.1261957938821218 1.4716246269355877 0.0857527059362301 27845 0.10099391387012048 1.4716246269355875 0.0686274964563643 40706 0.09978740115949346 1.4716246269355875 0.06780764560000878 6891 0.09946999111448288 1.4716246269355875 0.06759195877389775 22035 0.09922096273584567 1.4716246269355877 0.06742273873362445 39275 0.09587321405751065 1.4716246269355875 0.06514787283571803 49175 0.08720084803019994 1.4716246269355873 0.05925481704650536 47209 0.08716925205337936 1.4716246269355875 0.05923334691326467 44628 0.08596757192823058 1.4716246269355875 0.0584167799007575 48679 0.08596757192823058 1.4716246269355875 0.0584167799007575 37119 0.08559952940999721 1.4716246269355873 0.058166687240240024 12023 0.08329844927693023 1.4716246269355875 0.05660305471401721 27156 0.08288295244269753 1.4716246269355873 0.05632071584401754 15438 0.08288295244269753 1.4716246269355875 0.05632071584401753 41544 0.08278574038807636 1.4716246269355875 0.05625465820075588 30391 0.08247335140660675 1.4716246269355875 0.05604238329331559 4025 0.08137884587711594 1.4716246269355873 0.05529864368101382 3376 0.08137884587711594 1.4716246269355873 0.05529864368101382 13577 0.08137884587711594 1.4716246269355873 0.05529864368101382 20310 0.08137884587711594 1.4716246269355873 0.05529864368101382 29926 0.08137884587711594 1.4716246269355873 0.05529864368101382 8362 0.08137884587711594 1.4716246269355873 0.05529864368101382 14804 0.08137884587711594 1.4716246269355873 0.05529864368101382 37514 0.08137884587711594 1.4716246269355873 0.05529864368101382 46011 0.08137884587711594 1.4716246269355875 0.055298643681013816 40110 0.08137884587711594 1.4716246269355875 0.055298643681013816 7539 0.08137884587711594 1.4716246269355875 0.055298643681013816 22217 0.08137884587711594 1.4716246269355875 0.055298643681013816 132 0.08137884587711594 1.4716246269355875 0.055298643681013816 38481 0.08137884587711594 1.4716246269355875 0.055298643681013816 274 0.08137884587711594 1.4716246269355875 0.055298643681013816 4477 0.08137884587711594 1.4716246269355875 0.055298643681013816 44399 0.08137884587711594 1.4716246269355875 0.055298643681013816 31990 0.08137884587711594 1.4716246269355875 0.055298643681013816 32426 0.08137884587711594 1.4716246269355875 0.055298643681013816 22721 0.08137884587711594 1.4716246269355875 0.055298643681013816 17284 0.08137884587711594 1.4716246269355875 0.055298643681013816 24230 0.08137884587711594 1.4716246269355875 0.055298643681013816 38288 0.08137884587711594 1.4716246269355875 0.055298643681013816 27219 0.08137884587711594 1.4716246269355875 0.055298643681013816 40377 0.08137884587711594 1.4716246269355875 0.055298643681013816 1203 0.08137884587711594 1.4716246269355875 0.055298643681013816 33407 0.08137884587711594 1.4716246269355875 0.055298643681013816 11109 0.08137884587711594 1.4716246269355875 0.055298643681013816 47911 0.08137884587711594 1.4716246269355875 0.055298643681013816 10451 0.08137884587711594 1.4716246269355875 0.055298643681013816 29406 0.08137884587711594 1.4716246269355875 0.055298643681013816 15008 0.08137884587711594 1.4716246269355

In [0]:
# retreive actual ratings from this user
user_product_ratings = (
  spark
    .table('instacart.user_ratings')
    .filter("user_id = 148 and split = 'calibration'")
  )

# combine with recommender ratings
product_ratings_for_user = (
    product_ratings
      .join( user_product_ratings, on='product_id', how='outer')
      .selectExpr('product_id', 'COALESCE(normalized_purchases, 0.0) as user_score', 'recommendation_score')
      .orderBy('recommendation_score', ascending=False)
  )

display(product_ratings_for_user)

product_id user_score recommendation_score 24413 0.24413653763134782 0.2620726465779026 31504 0.32551538350846376 0.23599022052571375 44557 0.24413653763134782 0.22838318030139856 18629 0.16275769175423188 0.1977178365815551 21806 0.24413653763134782 0.1857796765671384 10983 0.16275769175423188 0.11059728736202765 23383 0.16275769175423188 0.11059728736202765 20632 0.16275769175423188 0.11059728736202763 23459 0.16275769175423188 0.11059728736202763 7412 0.16275769175423188 0.11059728736202763 7870 0.16275769175423188 0.11059728736202763 17450 0.16275769175423188 0.11059728736202763 17828 0.16275769175423188 0.11059728736202763 11212 0.08137884587711594 0.0857527059362301 27845 0.08137884587711594 0.0686274964563643 40706 0.08137884587711594 0.06780764560000878 6891 0.08137884587711594 0.06759195877389775 22035 0.08137884587711594 0.06742273873362445 39275 0.08137884587711594 0.06514787283571803 49175 0.08137884587711594 0.05925481704650536 47209 0.08137884587711594 0.05923334691326467 48679 0.08137884587711594 0.0584167799007575 44628 0.08137884587711594 0.0584167799007575 37119 0.08137884587711594 0.058166687240240024 12023 0.08137884587711594 0.05660305471401721 27156 0.08137884587711594 0.05632071584401754 15438 0.08137884587711594 0.05632071584401753 41544 0.08137884587711594 0.05625465820075588 30391 0.08137884587711594 0.05604238329331559 14804 0.08137884587711594 0.05529864368101382 20310 0.08137884587711594 0.05529864368101382 3376 0.08137884587711594 0.05529864368101382 8362 0.08137884587711594 0.05529864368101382 4025 0.08137884587711594 0.05529864368101382 13577 0.08137884587711594 0.05529864368101382 29926 0.08137884587711594 0.05529864368101382 37514 0.08137884587711594 0.05529864368101382 4477 0.08137884587711594 0.055298643681013816 7539 0.08137884587711594 0.055298643681013816 22217 0.08137884587711594 0.055298643681013816 28568 0.08137884587711594 0.055298643681013816 32426 0.08137884587711594 0.055298643681013816 38481 0.08137884587711594 0.055298643681013816 40110 0.08137884587711594 0.055298643681013816 132 0.08137884587711594 0.055298643681013816 46011 0.08137884587711594 0.055298643681013816 31990 0.08137884587711594 0.055298643681013816 44399 0.08137884587711594 0.055298643681013816 34524 0.08137884587711594 0.055298643681013816 38288 0.08137884587711594 0.055298643681013816 1203 0.08137884587711594 0.055298643681013816 38567 0.08137884587711594 0.055298643681013816 39166 0.08137884587711594 0.055298643681013816 1915 0.08137884587711594 0.055298643681013816 46069 0.08137884587711594 0.055298643681013816 40377 0.08137884587711594 0.055298643681013816 47911 0.08137884587711594 0.055298643681013816 10451 0.08137884587711594 0.055298643681013816 5201 0.08137884587711594 0.055298643681013816 11109 0.08137884587711594 0.055298643681013816 15008 0.08137884587711594 0.055298643681013816 17284 0.08137884587711594 0.055298643681013816 20564 0.08137884587711594 0.055298643681013816 21295 0.08137884587711594 0.055298643681013816 22721 0.08137884587711594 0.055298643681013816 24230 0.08137884587711594 0.055298643681013816 781 0.08137884587711594 0.055298643681013816 24118 0.08137884587711594 0.055298643681013816 25821 0.08137884587711594 0.055298643681013816 26313 0.08137884587711594 0.055298643681013816 27219 0.08137884587711594 0.055298643681013816 29406 0.08137884587711594 0.055298643681013816 30461 0.08137884587711594 0.055298643681013816 33407 0.08137884587711594 0.055298643681013816 274 0.08137884587711594 0.055298643681013816 19385 0.08137884587711594 0.05529864368101381 29871 0.08137884587711594 0.05529864368101381 29721 0.08137884587711594 0.05529864368101381 32420 0.08137884587711594 0.05529864368101381 36953 0.08137884587711594 0.05529864368101381 41699 0.08137884587711594 0.05529864368101381 42294 0.08137884587711594 0.05529864368101381 47205 0.08137884587711594 0.05529864368101381 10129 0.08137884587711594 0.05529864368101381 26638 0.08137884587711594 0.05529864368101381 13176 0.0 0.03327217161795129 24

In [0]:
max_partition_count = sc.defaultParallelism * 100
spark.conf.set('spark.sql.shuffle.partitions', max_partition_count) 

In [0]:
# ratio of customers to sample
sample_fraction = 0.10

# calculate max possible distance between users
max_distance = math.sqrt(2)

# calculate min possible similarity (unscaled)
min_score = 1 / (1 + math.sqrt(2))

# remove any old comparisons that might exist
shutil.rmtree('/dbfs/mnt/instacart/gold/similarity_results', ignore_errors=True)

# perform similarity join for sample of users
sample_comparisons = (
  fitted_lsh.approxSimilarityJoin(
    hashed_vectors.sample(withReplacement=False, fraction=sample_fraction), # use a random sample for our target users
    hashed_vectors,
    threshold = max_distance,
    distCol = 'distance'
    )
    .withColumn('similarity', lit(1)/(lit(1)+col('distance')))
    .withColumn('similarity_rescaled', (col('similarity') - lit(min_score)) / lit(1.0 - min_score))
    .selectExpr(
      'datasetA.user_id as user_a',
      'datasetB.user_id as user_b',
      'similarity_rescaled as similarity'
      )
  )

# write output for reuse
(
  sample_comparisons
    .write
    .format('delta')
    .mode('overwrite')
    .save('/mnt/instacart/gold/similarity_results')
  )

display(
  spark.table( 'DELTA.`/mnt/instacart/gold/similarity_results`' )
  )

In [0]:
number_of_customers = 10

# get k number of similar users for each sample user
similar_users =  (
    spark.sql('''
      SELECT 
        user_a, 
        user_b, 
        similarity
      FROM (
        SELECT
          user_a,
          user_b,
          similarity,
          ROW_NUMBER() OVER (PARTITION BY user_a ORDER BY similarity DESC) as seq
        FROM DELTA.`/mnt/instacart/gold/similarity_results`
        )
      WHERE seq <= {0}
      '''.format(number_of_customers)
      )
    )

similar_users = similar_users.createOrReplaceTempView('similar_users')
display(similar_users)

In [0]:
similar_ratings = spark.sql('''
    SELECT
      m.user_a,
      m.user_b,
      m.product_id,
      COALESCE(n.normalized_purchases, 0.0) as normalized_purchases,
      m.similarity
    FROM (
      SELECT
        x.user_a,
        x.user_b,
        y.product_id,
        x.similarity
      FROM similar_users x
      CROSS JOIN instacart.products y
      ) m
    LEFT OUTER JOIN ( -- retrieve ratings actually provided by similar users
      SELECT 
        user_id as user_b, 
        product_id, 
        normalized_purchases 
      FROM instacart.user_ratings
      WHERE split = 'calibration'
        ) n
      ON m.user_b=n.user_b AND m.product_id=n.product_id
      ''')

display(similar_ratings)

In [0]:
product_ratings = ( 
   similar_ratings
    .groupBy('user_a','product_id')
      .agg( 
        sum(col('normalized_purchases') * col('similarity')).alias('weighted_rating'),
        sum('similarity').alias('total_weight')
        )
    .withColumn('recommendation_score', col('weighted_rating')/col('total_weight'))
    .select('user_a', 'product_id', 'recommendation_score')
    .orderBy(['user_a','recommendation_score'], ascending=[True,False])
  )

product_ratings.createOrReplaceTempView('product_ratings')

display(
  product_ratings
  )  

In [0]:
%sql

SELECT
  user_a as user_id,
  product_id,
  recommendation_score,
  PERCENT_RANK() OVER (PARTITION BY user_a ORDER BY recommendation_score DESC) as rank_ui
FROM product_ratings
ORDER BY user_a, recommendation_score DESC

In [0]:
eval_set = (
  spark
    .sql('''
    SELECT 
      x.user_id,
      x.product_id,
      x.r_t_ui,
      y.rank_ui
    FROM (
      SELECT
        user_id,
        product_id,
        normalized_purchases as r_t_ui
      FROM instacart.user_ratings 
      WHERE split = 'evaluation' -- the test period
        ) x
    INNER JOIN (
      SELECT
        user_a as user_id,
        product_id,
        PERCENT_RANK() OVER (PARTITION BY user_a ORDER BY recommendation_score DESC) as rank_ui
      FROM product_ratings
      ) y
      ON x.user_id=y.user_id AND x.product_id=y.product_id
      ''').cache()
  )

display(
  eval_set
    .withColumn('weighted_r', col('r_t_ui') * col('rank_ui') )
    .groupBy()
      .agg(
        sum('weighted_r').alias('numerator'),
        sum('r_t_ui').alias('denominator')
        )
    .withColumn('mean_percent_rank', col('numerator')/col('denominator'))
    .select('mean_percent_rank')
  )

In [0]:
%sql

SELECT
  product_id,
  PERCENT_RANK() OVER (ORDER BY normalized_purchases DESC) as rank_ui
FROM (
  SELECT
    x.product_id,
    COALESCE(y.normalized_purchases,0.0) as normalized_purchases
  FROM (SELECT product_id FROM instacart.products) x
  LEFT OUTER JOIN instacart.naive_ratings y
    ON x.product_id=y.product_id
  WHERE split = 'calibration'
  )

product_id rank_ui 24852 0.0 13176 2.0130445285449713E-5 21137 4.0260890570899426E-5 21903 6.0391335856349146E-5 47209 8.052178114179885E-5 47766 1.0065222642724857E-4 47626 1.2078267171269829E-4 16797 1.40913116998148E-4 26209 1.610435622835977E-4 27845 1.8117400756904742E-4 27966 2.0130445285449714E-4 22935 2.2143489813994686E-4 24964 2.4156534342539658E-4 45007 2.616957887108463E-4 39275 2.81826233996296E-4 49683 3.019566792817457E-4 28204 3.220871245671954E-4 5876 3.422175698526451E-4 8277 3.6234801513809485E-4 40706 3.8247846042354457E-4 4920 4.026089057089943E-4 30391 4.22739350994444E-4 45066 4.428697962798937E-4 42265 4.6300024156534344E-4 49235 4.8313068685079316E-4 44632 5.032611321362429E-4 19057 5.233915774216926E-4 4605 5.435220227071423E-4 37646 5.63652467992592E-4 21616 5.837829132780418E-4 17794 6.039133585634914E-4 27104 6.240438038489411E-4 30489 6.441742491343908E-4 31717 6.643046944198405E-4 27086 6.844351397052903E-4 44359 7.0456558499074E-4 28985 7.246960302761897E-4 46979 7.448264755616394E-4 8518 7.649569208470891E-4 41950 7.850873661325389E-4 26604 8.052178114179886E-4 5077 8.253482567034383E-4 34126 8.45478701988888E-4 22035 8.656091472743377E-4 39877 8.857395925597874E-4 35951 9.058700378452372E-4 43352 9.260004831306869E-4 10749 9.461309284161366E-4 19660 9.662613737015863E-4 9076 9.86391818987036E-4 21938 0.0010065222642724858 43961 0.0010266527095579355 24184 0.0010467831548433852 34969 0.001066913600128835 46667 0.0010870440454142846 48679 0.0011071744906997344 25890 0.001127304935985184 31506 0.0011474353812706338 12341 0.0011675658265560835 39928 0.001187696271841533 24838 0.0012078267171269827 5450 0.0012279571624124325 22825 0.0012480876076978822 5785 0.001268218052983332 35221 0.0012883484982687816 28842 0.0013084789435542313 33731 0.001328609388839681 27521 0.0013487398341251308 44142 0.0013688702794105805 33198 0.0013890007246960302 8174 0.00140913116998148 20114 0.0014292616152669297 8424 0.0014493920605523794 27344 0.001469522505837829 11520 0.0014896529511232788 29487 0.0015097833964087285 18465 0.0015299138416941783 28199 0.001550044286979628 15290 0.0015701747322650777 46906 0.0015903051775505274 9839 0.0016104356228359771 27156 0.0016305660681214269 3957 0.0016506965134068766 43122 0.0016708269586923263 23909 0.001690957403977776 34358 0.0017110878492632257 4799 0.0017312182945486755 9387 0.0017513487398341252 16759 0.001771479185119575 196 0.0017916096304050246 42736 0.0018117400756904743 38689 0.001831870520975924 4210 0.0018520009662613738 41787 0.0018721314115468235 41220 0.0018922618568322732 47144 0.001912392302117723 7781 0.0019325227474031727 33000 0.0019526531926886224 20995 0.001972783637974072 21709 0.001992914083259522 19678 0.0020130445285449715 40604 0.0020331749738304213 30233 0.002053305419115871 34243 0.0020734358644013207 37687 0.0020935663096867704 24489 0.00211369675497222 42828 0.00213382720025767 5479 0.0021539576455431196 432 0.0021740880908285693 6184 0.002194218536114019 16185 0.0022143489813994687 42768 0.0022344794266849185 17948 0.002254609871970368 33754 0.002274740317255818 19348 0.0022948707625412676 8193 0.0023150012078267173 26369 0.002335131653112167 42585 0.0023552620983976168 14992 0.002375392543683066 14947 0.0023955229889685158 22963 0.0024156534342539655 1463 0.002435783879539415 28849 0.002455914324824865 8021 0.0024760447701103147 25659 0.0024961752153957644 21405 0.002516305660681214 46676 0.002536436105966664 31343 0.0025565665512521135 41844 0.0025766969965375633 38293 0.002596827441823013 42701 0.0026169578871084627 43789 0.0026370883323939124 36011 0.002657218777679362 5025 0.002677349222964812 39475 0.0026974796682502616 43295 0.0027176101135357113 11777 0.002737740558821161 20842 0.0027578710041066107 32689 0.0027780014493920605 32655 0.00279813189467751 2295 0.00281826233996296 13870 0.0028383927852484096 46802 0.0028383927852484096 25146 0.002878653675819309 18531 0.0028987841211047588 5212 0.0029189145663902085 31553 0.00293904501167

In [0]:
%sql

SELECT
  SUM(r_t_ui * rank_ui) / SUM(rank_ui) as mean_percent_rank
FROM (
  SELECT 
    x.user_id,
    x.product_id,
    x.r_t_ui,
    y.rank_ui
  FROM (
    SELECT
      p.user_id,
      p.product_id,
      p.normalized_purchases as r_t_ui
    FROM instacart.user_ratings p
    INNER JOIN (SELECT DISTINCT user_a as user_id FROM similar_users) q
      ON p.user_id=q.user_id
    WHERE p.split = 'evaluation' -- the test period
      ) x
  INNER JOIN (
    SELECT
      product_id,
      PERCENT_RANK() OVER (ORDER BY normalized_purchases DESC) as rank_ui
    FROM (
      SELECT
        x.product_id,
        COALESCE(y.normalized_purchases,0.0) as normalized_purchases
      FROM (SELECT product_id FROM instacart.products) x
      LEFT OUTER JOIN instacart.naive_ratings y
        ON x.product_id=y.product_id
      WHERE split = 'calibration'
      )
    ) y
    ON x.product_id=y.product_id
    )

In [0]:
def list_cached_dataframes():
    return [(k,v) for (k,v) in [(k,v) for (k, v) in globals().items() if isinstance(v, DataFrame)] if v.is_cached]
  
for name, obj in list_cached_dataframes():
  obj.unpersist()